# Классификация комментариев

**Цель работы** — натренировать модель, классифицирующую коментарии на позитивные и негативные. Данный функционал требуется заказчику — интернет-магазину, чтобы находить токсичные комментарии на их новом сервисе, позволяющем комментировать описания товаров, созданные/отредактированные другими пользователями, после чего отправлять найденные комментарии на модерацию.

Метрика качества F-1 должна быть не менее 0.75.

Предоставлен набор текстовых данных с разметкой об их токичности.

**Ход работы**

Загрузим и подготовим данные, после чего получим их эмбеддинги с помощью BERT-модели.

Далее попробуем разные классификационные модели, подбирая их гиперпараметры с помощью кросс-валидации.

Сравним качество моделей, выберем лучшую, после чего проверим её на тестовых данных. Сформулируем итоговый вывод.
 
Таким образом работа будет состоять из следующих этапов:

<h1>Содержание<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Загрузка-и-подготовка-данных" data-toc-modified-id="Загрузка-и-подготовка-данных-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Загрузка и подготовка данных</a></span><ul class="toc-item"><li><span><a href="#Просмотр-данных" data-toc-modified-id="Просмотр-данных-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Просмотр данных</a></span></li><li><span><a href="#Предобработка-и-подготовка-данных" data-toc-modified-id="Предобработка-и-подготовка-данных-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Предобработка и подготовка данных</a></span></li></ul></li><li><span><a href="#Получение-эмбеддингов" data-toc-modified-id="Получение-эмбеддингов-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Получение эмбеддингов</a></span></li><li><span><a href="#Выбор-наилучшей-модели" data-toc-modified-id="Выбор-наилучшей-модели-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Выбор наилучшей модели</a></span></li><li><span><a href="#Проверка-качества-итоговой-модели" data-toc-modified-id="Проверка-качества-итоговой-модели-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Проверка качества итоговой модели</a></span></li><li><span><a href="#Общий-вывод" data-toc-modified-id="Общий-вывод-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Общий вывод</a></span></li></ul></div>

## Загрузка и подготовка данных

In [2]:
import os
import re
import random

import numpy as np
import pandas as pd
from tqdm.auto import tqdm
import plotly.express as px
from plotly.figure_factory import create_annotated_heatmap

from tune_sklearn import TuneSearchCV
from sklearn.metrics import \
    f1_score, \
    roc_auc_score, \
    accuracy_score, \
    confusion_matrix, \
    fbeta_score, \
    make_scorer
from sklearn.model_selection import \
    train_test_split, \
    ShuffleSplit, \
    GridSearchCV

from sklearn.linear_model import LogisticRegression
from lightgbm import LGBMClassifier
import torch
from torch.nn import init
from torch import nn, optim
from skorch.classifier import NeuralNetBinaryClassifier
from skorch.callbacks import EpochScoring, EarlyStopping, LRScheduler
from transformers import AutoTokenizer, AutoModel

In [3]:
os.environ['CUBLAS_WORKSPACE_CONFIG']=':4096:8'
def set_seed(seed):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    torch.use_deterministic_algorithms(True)
    torch.backends.cudnn.deterministic = True
SEED = 3
set_seed(SEED)
if torch.cuda.is_available():
    device = 'cuda'
else:
    device = 'cpu'

### Просмотр данных

Взглянем на основные характеристики датасета.

In [4]:
comments = pd.read_csv('/datasets/toxic_comments.csv')
display(
    comments.head(10),
    comments.sample(10, random_state=SEED),
    comments.info()
    )

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 159292 entries, 0 to 159291
Data columns (total 3 columns):
 #   Column      Non-Null Count   Dtype 
---  ------      --------------   ----- 
 0   Unnamed: 0  159292 non-null  int64 
 1   text        159292 non-null  object
 2   toxic       159292 non-null  int64 
dtypes: int64(2), object(1)
memory usage: 3.6+ MB


Unnamed: 0                                               text  toxic
0           0  Explanation\nWhy the edits made under my usern...      0
1           1  D'aww! He matches this background colour I'm s...      0
2           2  Hey man, I'm really not trying to edit war. It...      0
3           3  "\nMore\nI can't make any real suggestions on ...      0
4           4  You, sir, are my hero. Any chance you remember...      0
5           5  "\n\nCongratulations from me as well, use the ...      0
6           6       COCKSUCKER BEFORE YOU PISS AROUND ON MY WORK      1
7           7  Your vandalism to the Matt Shirvington article...      0
8           8  Sorry if the word 'nonsense' was offensive to ...      0
9           9  alignment on this subject and which are contra...      0

Unnamed: 0                                               text  toxic
62430        62497  caden s should b shot in the head 100x u best ...      1
67067        67135                           New criticism, comments,      0
64304        64371  Re: Yo \n\nHey, I am never on this anymore, on...      0
60832        60899  . Science will progress, as always, without th...      0
134205      134343  There would still be considered heels, regardl...      0
119807      119912  Hey, no problem. Let me know if you need any m...      0
139157      139309  Thank You\nThanks, Ed.  I did not realise that...      0
72627        72698  Yea, looked you up, no huge skeletons in my vi...      0
89366        89449  YOU SUCK IT!!! AS YOU'RE USED TO SUCK PHALLUS,...      1
95943        96035  BTW, I think this should say something about t...      0

None

Посмотрим также на распределение таргета, присутствует ли дисбаланс классов?

In [5]:
px.pie(
    comments,
    names=comments.toxic.replace({1: 'Токсичные', 0: 'Не токсичные'})
    ).update_traces(
        textinfo='percent+label',
        insidetextorientation='tangential'
        ).update_layout(
            uniformtext_minsize=15,
            uniformtext_mode='hide',
            width=1000,
            height=500,
            showlegend=False,
            title=dict(
                text='Токсичность комментариев',
                x=.5,
                font_size=20
                )
            )

**Промежуточные выводы**

По результатам изучения датасета можно выделить следующие моменты:

Во-первых, имеется столбец, поначалу дублирующий индексы, но со временем его значения становятся больше соответствующих индексов, что может говорить о том, что некоторое количество записей относительно изнчальных данных было удалено, либо утеряно. Можно обратиться к заказчику для возможного восстановления недостающих данных.

Во-вторых, виден достаточно сильный дисбаланс классов: токсичных комментариев только 10% от всех данных, нужно будет учесть это при разделении данных на выборки и обучении моделей.

В-третьих, в текстах присутствуют различные служебные символы. Избавимся от них перед передачей данных токенизатору. Переводить данные в нижний регистр или удалять стоп-слова, учитывая используемую далее BERT-модель, нет необходимости.

### Предобработка и подготовка данных

Очистим данные от служебных символов, после чего токенезируем тексты для последующей генерации их эмбеддингов. Для лучшего качества будем использовать модель из семейства BERT, предобученную конкретно на токсичных текстах.

In [6]:
def cleaning(text):
    clean_text = re.sub(r'\s+', ' ', text).strip()
    clean_text = re.sub(r'"', '', clean_text)
    return clean_text

comments.text = comments.text.apply(lambda x: cleaning(x))
comments.sample(10, random_state=SEED)

Unnamed: 0                                               text  toxic
62430        62497  caden s should b shot in the head 100x u best ...      1
67067        67135                           New criticism, comments,      0
64304        64371  Re: Yo Hey, I am never on this anymore, only w...      0
60832        60899  . Science will progress, as always, without th...      0
134205      134343  There would still be considered heels, regardl...      0
119807      119912  Hey, no problem. Let me know if you need any m...      0
139157      139309  Thank You Thanks, Ed. I did not realise that. ...      0
72627        72698  Yea, looked you up, no huge skeletons in my vi...      0
89366        89449  YOU SUCK IT!!! AS YOU'RE USED TO SUCK PHALLUS,...      1
95943        96035  BTW, I think this should say something about t...      0

In [7]:
tokenizer = AutoTokenizer.from_pretrained('unitary/toxic-bert')
tokens = torch.LongTensor(comments.text.apply(lambda x: tokenizer.encode(
    x,
    add_special_tokens=True,
    padding='max_length',
    truncation=True
    ))).to(device)
attention_mask = torch.where(tokens != 0, 1, 0).to(device)

## Получение эмбеддингов

In [8]:
%%time
model = AutoModel.from_pretrained('unitary/toxic-bert').to(device)
batch_size = 300
embeddings = []
for i in tqdm(range(tokens.shape[0] // batch_size)):
        batch = tokens[batch_size*i:batch_size*(i+1)]
        attention_mask_batch = attention_mask[batch_size*i:batch_size*(i+1)]
        
        with torch.no_grad():
            batch_embeddings = model(
                batch,
                attention_mask=attention_mask_batch
                )
        embeddings.append(batch_embeddings[0][:,0,:].cpu().numpy())

Some weights of the model checkpoint at unitary/toxic-bert were not used when initializing BertModel: ['classifier.bias', 'classifier.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


  0%|          | 0/530 [00:00<?, ?it/s]

CPU times: total: 3min 54s
Wall time: 11min 18s


In [9]:
features = np.concatenate(embeddings)
target = comments.toxic[:features.shape[0]]
train_features, test_features, train_target, test_target = (
    train_test_split(
        features,
        target,
        test_size=.15,
        stratify=target,
        random_state=SEED
        )
    )
print(
    'Размеры тренировочной и тестовой выборок с эмбеддингами: ',
    train_features.shape,
    test_features.shape,
    '\n',
    'Размеры тренировочной и тестовой выборок с целевым признаком: ',
    train_target.shape,
    test_target.shape
    )

Размеры тренировочной и тестовой выборок с эмбеддингами:  (135150, 768) (23850, 768) 
 Размеры тренировочной и тестовой выборок с целевым признаком:  (135150,) (23850,)


## Выбор наилучшей модели

Натренируем следующие разные модели: логистическую регресию, градиентный бустинг, а также дообученную под конкретно наши тексты модель BERT, полученную путём применения к эмбеддингам линейного слоя нейросети. После подбора гиперпараметров выберем лучшую из них.

In [10]:
metrics = pd.DataFrame(
    index=['f-beta'],
    columns=['LR', 'GB', 'NN']
    )
ss = ShuffleSplit(n_splits=5, test_size=.2, random_state=SEED)
scorer = make_scorer( # для поиска гиперпараметров используем
    fbeta_score,      # несколько смещённую f-beta метрику,
    beta=1.1          # учитывая оставшийся дисбаланс классов
    )

In [11]:
%%time
lr_params = {
    'class_weight': ['balanced', None], # как и в случае с бустингом,
    'solver': ['lbfgs', 'sag'],         # протестируем веса классов,
    'C': (.001, 2)                      # сбалансированные по их соотношению
    }
lr_model=LogisticRegression(random_state=SEED)
best_lr_model = TuneSearchCV(
    lr_model,
    lr_params,
    scoring=scorer,
    cv=ss,
    random_state=SEED,
    n_trials=100,
    n_jobs=18,
    search_optimization='hyperopt'
    )
best_lr_model.fit(train_features, train_target)
metrics.loc['f-beta', 'LR'] = best_lr_model.best_score_
print(
    'Лучшие параметры для логистической регрессии:',
    best_lr_model.best_params_
    )

(_Trainable pid=28824) c:\ProgramData\Anaconda3\envs\default\lib\site-packages\sklearn\linear_model\_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
(_Trainable pid=28824) STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.
(_Trainable pid=28824) 
(_Trainable pid=28824) Increase the number of iterations (max_iter) or scale the data as shown in:
(_Trainable pid=28824)     https://scikit-learn.org/stable/modules/preprocessing.html
(_Trainable pid=28824) Please also refer to the documentation for alternative solver options:
(_Trainable pid=28824)     https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
(_Trainable pid=28824)   n_iter_i = _check_optimize_result(
(_Trainable pid=17968) c:\ProgramData\Anaconda3\envs\default\lib\site-packages\sklearn\linear_model\_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
(_Trainable pid=17968) STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.
(_Trainable pid=17968) 
(_Trainable pid=17968)

Лучшие параметры для логистической регрессии: {'C': 0.09921598648443161, 'class_weight': None, 'solver': 'lbfgs'}
CPU times: total: 29.6 s
Wall time: 25min 51s


c:\ProgramData\Anaconda3\envs\default\lib\site-packages\sklearn\linear_model\_logistic.py:458: ConvergenceWarning:

lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression



In [12]:
%%time
gb_params = {
    'boosting_type': ['gbdt', 'dart', 'goss'],
    'is_unbalance': [True, False],
    'n_estimators': list(range(500, 1001)),
    'min_child_samples': list(range(10, 51)),
    'learning_rate': (.01, .16)
    }
gb_model = LGBMClassifier(
    random_state=SEED,
    force_col_wise=True,
    verbosity=-1
    )
best_gb_model = TuneSearchCV(
    gb_model,
    gb_params,
    scoring=scorer,
    cv=ss,
    random_state=SEED,
    n_trials=100,
    n_jobs=-1,
    search_optimization='bohb'
    )
best_gb_model.fit(train_features, train_target)
metrics.loc['f-beta', 'GB'] = best_gb_model.best_score_
print(
    'Лучшие параметры для градиентного бустинга:',
    best_gb_model.best_params_
    )

Лучшие параметры для градиентного бустинга: {'boosting_type': 'dart', 'is_unbalance': False, 'learning_rate': 0.04202803974826657, 'min_child_samples': 44, 'n_estimators': 920}
CPU times: total: 14min 2s
Wall time: 2h 55min 43s


In [13]:
f_train = torch.FloatTensor(train_features)
f_test = torch.FloatTensor(test_features)

t_train = torch.FloatTensor(train_target.values)
t_test = torch.FloatTensor(test_target.values)

In [14]:
class Net(nn.Module):
    def __init__(
        self,
        weight_init,
        bias_init,
        n_in_neurons=768,
        n_out_neurons=1
        ):
        super().__init__()

        self.fc = nn.Linear(n_in_neurons, n_out_neurons)

        weight_init(self.fc.weight)
        bias_init(self.fc.bias)

    def forward(self, x):
        x = self.fc(x)
        return x

net = NeuralNetBinaryClassifier(
    module=Net,
    verbose=0,
    lr=5e-2,
    batch_size=-1,
    max_epochs=500,
    callbacks=[
        EpochScoring(
            scoring=scorer,
            lower_is_better=False,
            name='F1'
            ),
        EarlyStopping(
            lower_is_better=False,
            monitor='F1',
            patience=30,
            load_best=True
            ),
        LRScheduler(
            policy=optim.lr_scheduler.CosineAnnealingWarmRestarts,
            monitor='F1',
            T_0=15
            )
        ]
    )

In [15]:
%%time
nn_params = {
    'module__weight_init': [
        nn.init.xavier_uniform_,
        nn.init.xavier_normal_,
        nn.init.kaiming_uniform_,
        nn.init.kaiming_normal_
        ],
    'module__bias_init': [
        nn.init.uniform_,
        nn.init.normal_
        ],
    'optimizer': [
        optim.Adam,
        optim.AdamW,
        optim.Adamax,
        optim.RAdam,
        optim.NAdam
        ]
    }
best_nn_model = GridSearchCV(
    net,
    nn_params,
    scoring=scorer,
    cv=ss,
    n_jobs=-1
    )
best_nn_model.fit(f_train, t_train)
metrics.loc['f-beta', 'NN'] = best_nn_model.best_score_
print(
    'Лучшие параметры для нейронной сети:',
    best_nn_model.best_params_
    )

Лучшие параметры для нейронной сети: {'module__bias_init': <function uniform_ at 0x000001479A773520>, 'module__weight_init': <function xavier_normal_ at 0x000001479A773B50>, 'optimizer': <class 'torch.optim.radam.RAdam'>}
CPU times: total: 3min 45s
Wall time: 41min 35s


Взглянем на получившиеся метрики.

In [16]:
metrics

LR        GB        NN
f-beta  0.9449  0.943843  0.940294

**Промежуточные выводы**

Все модели показали примерно одинаковое качество. Чуть лучше оказался алгоритм логистической регресии, соответствующую модель и выберем в качестве итоговой.

## Проверка качества итоговой модели

При финальном тестировании, кроме **F-1**, посмотрим на показатели метрик **Accuracy** и **AUC-ROC**, а также на матрицу ошибок, чтобы более комплексно понимать, насколько хорошо в принципе справляется с предсказаниями наша модель.

In [17]:
preds = best_lr_model.predict(test_features)
conf_mx = pd.DataFrame(confusion_matrix(test_target, preds))
conf_mx.loc[0, 2] = conf_mx.loc[1, 1] / (conf_mx.loc[1, 1] + conf_mx.loc[0, 1])
conf_mx.loc[1, 2] = conf_mx.loc[1, 1] / (conf_mx.loc[1, 1] + conf_mx.loc[1, 0])

fig = create_annotated_heatmap(
    conf_mx.to_numpy().round(3),
    x = ['0', '1', 'Precision/Recall'],
    y = ['1', '0']
    ).update_layout(
        width=1000,
        height=500,
        xaxis_title='Предсказания',
        yaxis_title='Истинные значения',
        title=dict(
            text='Марица ошибок на тестовых данных',
            x=.5,
            y=.95
            )
        ).update_xaxes(title_standoff=5)
fig.show()
print()
print('F-1 на тестовых данных', f1_score(test_target, preds).round(3))
print(
    'Accuracy на тестовых данных',
    accuracy_score(test_target, preds).round(3)
    )
print(
    'AUC-ROC на тестовых данных',
    roc_auc_score(
        test_target,
        best_lr_model.predict_proba(test_features)[:, 1]
        ).round(3)
    )


F-1 на тестовых данных 0.95
Accuracy на тестовых данных 0.99
AUC-ROC на тестовых данных 0.998


## Общий вывод

В итоге требуемый порог значения метрики превышен, различные классификационные алгоритмы показали примерно одинаковое качество. Вероятно, это говорит в том числе о том, что ключевую роль в данном подходе играет именно качество полученных изначально трансформером эмбеддингов, которые в данном случае были общими для каждой "головы".
Значения дополнительно рассматриваемых метрик также являются высокими.

При использовании встроенных же методов алгоритмов для борьбы с дисбалансом в итоге оба раза модели показали качество хуже, чем без использования данных методов.

Для дальнейшего увеличения качества ещё можно пропробовать в том числе следующие операции:

* Использовать в качестве дополнительных обучающих записей в том числе отрезанные по максимально доступной длине части эмбеддингов, превысивших длину 768 (как минимум с примерами 1 класса)
* Попробовать другие оптимизаторы нейронной сети, более точно настроить параметры наилучшего из них
* Усложнить нейронную "голову" (добавить слоёв, перебрать, соответственно, к ним различные функции активаций, использовать батчнорм и т.д.)
* Повыстить количество итераций логистической регресии для лучшей сходимости решения
* Настроить дополнительные гиперпараметры градиентного бустинга

Заказчику же можно посоветовать лучше следить за сохранностью и полнотой собираемых данных, особенно более редких по целевому признаку.